In [1]:
# Transformers installation
! pip install -U accelerate
! pip install -U transformers
# To install from source instead of the last release, comment the command above and uncomment the following one.
# ! pip install git+https://github.com/huggingface/transformers.git

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 297.3/297.3 kB 3.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 23.7/23.7 MB 13.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 823.6/823.6 kB 35.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 14.1/14.1 MB 36.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 731.7/731.7 MB 1.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 410.6/410.6 MB 3.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 121.6/121.6 MB 8.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.5/56.5 MB 8.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 124.2/124.2 MB 8.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 196.0/196.0 MB 6.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 166.0/166.0 MB 6.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.1/99.1 kB 12.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━

In [2]:
!pip install datasets evaluate

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 510.5/510.5 kB 4.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 4.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 4.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 8.8 MB/s eta 0:00:00


## Carga del dataset

Login en HuggingFace

In [3]:
from huggingface_hub import notebook_login

notebook_login()

Carga del dataset 'climate_change'

In [ ]:
from datasets import load_dataset

climate_train = load_dataset("somosnlp/spa_climate_detection", split="train")
climate_test = load_dataset("somosnlp/spa_climate_detection", split="test")

climate_train[0]
climate_test[0]

{'text': 'Limitaciones inherentes al informe de sostenibilidad El informe de sostenibilidad de LG Chem se elabora para satisfacer las necesidades comunes de una amplia gama de usuarios y, por lo tanto, puede no incluir todos los aspectos del informe de sostenibilidad que cada usuario individual pueda considerar importantes en su propio entorno particular. Debido a las limitaciones inherentes a los controles internos, es posible que los controles de la empresa no impidan, o detecten y corrijan, todos los errores u omisiones en el procesamiento o la notificación de transacciones relacionadas con la memoria de sostenibilidad. Asimismo, la proyección de cualquier conclusión sobre un informe de sostenibilidad a periodos futuros está sujeta al riesgo de que los controles de la empresa se vuelvan inadecuados o fallen.',
 'label': 1}

## Preprocessing

In [4]:
from transformers import AutoTokenizer

tokenizer = AutoTokenizer.from_pretrained("bertin-project/bertin-roberta-base-spanish")

tokenizer_config.json:   0%|          | 0.00/1.12k [00:00<?, ?B/s]

vocab.json:   0%|          | 0.00/851k [00:00<?, ?B/s]

merges.txt:   0%|          | 0.00/509k [00:00<?, ?B/s]

tokenizer.json:   0%|          | 0.00/2.21M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/772 [00:00<?, ?B/s]

Funcion de preprocessing

In [ ]:
def preprocess_function(examples):
    return tokenizer(examples["text"], truncation=True)

tokenized_climate_train = climate_train.map(preprocess_function, batched=True)
tokenized_climate_test = climate_test.map(preprocess_function, batched=True)

Map:   0%|          | 0/780 [00:00<?, ? examples/s]

Batch of examples

In [ ]:
from transformers import DataCollatorWithPadding

data_collator = DataCollatorWithPadding(tokenizer=tokenizer)

## Evaluate

In [5]:
import evaluate

accuracy = evaluate.load("accuracy")

Funcion de evaluacion

In [6]:
import numpy as np


def compute_metrics(eval_pred):
    predictions, labels = eval_pred
    predictions = np.argmax(predictions, axis=1)
    return accuracy.compute(predictions=predictions, references=labels)

## Train

Ids to labels

In [7]:
id2label = {0: "NEGATIVE", 1: "POSITIVE"}
label2id = {"NEGATIVE": 0, "POSITIVE": 1}

Cargando el modelo

In [ ]:
from transformers import AutoModelForSequenceClassification, TrainingArguments, Trainer

model = AutoModelForSequenceClassification.from_pretrained(
    "bertin-project/bertin-roberta-base-spanish", num_labels=2, id2label=id2label, label2id=label2id
)

Some weights of RobertaForSequenceClassification were not initialized from the model checkpoint at bertin-project/bertin-roberta-base-spanish and are newly initialized: ['classifier.dense.bias', 'classifier.dense.weight', 'classifier.out_proj.bias', 'classifier.out_proj.weight']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
#!pip install transformers[torch]
!python -m pip install accelerate -U
!python -m pip install git+https://github.com/huggingface/accelerate

  Cloning https://github.com/huggingface/accelerate to /tmp/pip-req-build-b_p2h31n
  Running command git clone --filter=blob:none --quiet https://github.com/huggingface/accelerate /tmp/pip-req-build-b_p2h31n
  Resolved https://github.com/huggingface/accelerate to commit 16488be9a490e97012ccec5f466c8abc365258b1
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
  Created wheel for accelerate: filename=accelerate-0.30.0.dev0-py3-none-any.whl size=297391 sha256=c8efde1829c23f4c8ab743c8a739d2be761eb969e693f33c68975530a9b3325d
  Stored in directory: /tmp/pip-ephem-wheel-cache-c5x79bls/wheels/f6/c7/9d/1b8a5ca8353d9307733bc719107acb67acdc95063bba749f26
Successfully built accelerate
  Attempting uninstall: accelerate
    Found existing installation: accelerate 0.29.1
    Uninstalling accelerate-0.29.1:
      Successfully uninstalled accelerate-0.29.1


In [ ]:
!accelerate config

----------------------------------------------------------------------------------------------------In which compute environment are you running?
Please input a choice index (starting from 0), and press enter
 ➔  This machine
    AWS (Amazon SageMaker)
0
This machine
----------------------------------------------------------------------------------------------------Which type of machine are you using?
Please input a choice index (starting from 0), and press enter
 ➔  No distributed training
    multi-CPU
    multi-XPU
    multi-GPU
    multi-NPU
    multi-MLU
    TPU
0
No distributed training
Do you want to run your training on CPU only (even if a GPU / Apple Silicon / Ascend NPU device is available)? [yes/NO]:NO
Do you wish to optimize your script with torch dynamo?[yes/NO]:NO
Do you want to use DeepSpeed? [yes/NO]: NO
What GPU(s) (by id) should be used for training on this machine as a comma-seperated list? [all]:all
-------------------------------------------------------------------

In [ ]:
import accelerate

accelerate.__version__

'0.29.1'

In [ ]:
training_args = TrainingArguments(
    output_dir="bertin_base_climate_detection_spa_v2",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=2,
    weight_decay=0.01,
    evaluation_strategy="epoch",
    save_strategy="epoch",
    load_best_model_at_end=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_climate_train,
    eval_dataset=tokenized_climate_test,
    tokenizer=tokenizer,
    data_collator=data_collator,
    compute_metrics=compute_metrics,
)

trainer.train()

/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:436: FutureWarning: Passing the following arguments to `Accelerator` is deprecated and will be removed in version 1.0 of Accelerate: dict_keys(['dispatch_batches', 'split_batches', 'even_batches', 'use_seedable_sampler']). Please pass an `accelerate.DataLoaderConfiguration` instead: 
dataloader_config = DataLoaderConfiguration(dispatch_batches=None, split_batches=False, even_batches=True, use_seedable_sampler=True)
  warnings.warn(


TrainOutput(global_step=364, training_loss=0.16342690226795908, metrics={'train_runtime': 537.1898, 'train_samples_per_second': 10.797, 'train_steps_per_second': 0.678, 'total_flos': 1444660582776960.0, 'train_loss': 0.16342690226795908, 'epoch': 2.0})

In [ ]:
trainer.push_to_hub("somosnlp/bertin_base_climate_detection_spa_v2")

events.out.tfevents.1712507017.1bd3bc55f4f2.644.1:   0%|          | 0.00/5.94k [00:00<?, ?B/s]

model.safetensors:   0%|          | 0.00/499M [00:00<?, ?B/s]

Upload 4 LFS files:   0%|          | 0/4 [00:00<?, ?it/s]

events.out.tfevents.1712508046.1bd3bc55f4f2.644.2:   0%|          | 0.00/5.84k [00:00<?, ?B/s]

training_args.bin:   0%|          | 0.00/4.98k [00:00<?, ?B/s]

CommitInfo(commit_url='https://huggingface.co/Gerard-1705/bertin_base_climate_detection_spa_v2/commit/6ceb28407875279716e7fe7dc60b1253d5f71bd6', commit_message='somosnlp/bertin_base_climate_detection_spa_v2', commit_description='', oid='6ceb28407875279716e7fe7dc60b1253d5f71bd6', pr_url=None, pr_revision=None, pr_num=None)

## INFERENCE

In [41]:
from transformers import AutoTokenizer
tokenizer = AutoTokenizer.from_pretrained("somosnlp/bertin_base_climate_detection_spa_v2")
tokenizer.model_max_length
from transformers import AutoModelForSequenceClassification
import torch

model = AutoModelForSequenceClassification.from_pretrained("somosnlp/bertin_base_climate_detection_spa_v2")

In [43]:
tokenizer.model_max_length
tokenizer.model_max_length = 512

Validamos el modelo con un set de 200 rows

In [44]:
text = "El bioma dominante en Zambia es la sabana. Gran parte del centro, norte y oeste del país está ocupado por la ecorregión denominada sabana arbolada de miombo del Zambeze central. Al sureste se alternan la sabana arbolada de miombo meridional y la sabana arbolada de mopane del Zambeze."
inputs = tokenizer(text, return_tensors="pt")

In [45]:
with torch.no_grad():
    logits = model(**inputs).logits
predicted_class_id = logits.argmax().item()
model.config.id2label[predicted_class_id]

'NEGATIVE'

In [48]:
import pandas as pd
val_df = pd.read_csv("validation_dataset.csv", delimiter=';', on_bad_lines='warn')
print(val_df.shape)

(200, 1)


In [49]:
val_inputs = []
val_outputs = []
for txt in val_df['text']:
  print(txt)
  inputs = tokenizer(txt, return_tensors="pt", truncation=True)
  with torch.no_grad():
    logits = model(**inputs).logits
  predicted_class_id = logits.argmax().item()
  val_outputs.append(predicted_class_id)
  print(model.config.id2label[predicted_class_id])

El consumo de energía residencial aumenta rápidamente cada año debido a cambios demográficos y de comportamiento, como el aumento de la población y la adopción del trabajo desde casa tras el COVID-19. El elevado consumo de energía emite una cantidad sustancial de dióxido de carbono y otros gases de efecto invernadero, lo que contribuye al calentamiento global. Resulta crucial predecir con exactitud la carga residencial. Para permitir un control inteligente del consumo eléctrico doméstico, así como una generación, planificación y uso eficientes, predecimos el consumo energético doméstico a muy corto plazo, a corto plazo y a medio plazo utilizando datos de series temporales univariantes y multivariantes. Este estudio evalúa el impacto de diferentes unidades domésticas (calentador de agua y aire acondicionado), zonas (cocina, lavandería, despacho, salón, baño, cuarto de plancha, habitación de los adolescentes y habitación de los padres) y tiempo (es decir, hora, día y mes) en el consumo d

In [50]:
temp_eval = dict(output = val_outputs)
out_df = pd.DataFrame(temp_eval)
out_df.to_csv('out_eval.csv', sep=';', index=False)